In [1]:
!pip install pynrrd
!pip install ipywidgets
!pip install scipy
!pip install nbdev
!pip install fastai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.8/64.8 kB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.1/82.1 kB 4.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.1/58.1 kB 12.6 MB/s eta 0:00:00


In [6]:
conda install opencv

Retrieving notices: ...working... done
Solving environment: done

## Package Plan ##

  environment location: /home/isaac/mambaforge

  added / updated specs:
    - opencv


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    aom-3.5.0                  |       h27087fc_0         2.7 MB  conda-forge
    boltons-23.0.0             |     pyhd8ed1ab_0         296 KB  conda-forge
    conda-23.3.1               |  py310hff52083_0         941 KB  conda-forge
    ffmpeg-5.1.2               | gpl_h8dda1f0_106         9.2 MB  conda-forge
    freeglut-3.2.2             |       h9c3ff4c_1         162 KB  conda-forge
    gnutls-3.7.8               |       hf3e180e_0         2.2 MB  conda-forge
    hdf5-1.14.0                |nompi_hb72d44e_103         3.4 MB  conda-forge
    jasper-2.0.33              |       h0ff4b12_1         709 KB  conda-forge
    jsonpatch-1.32             |     pyhd8ed1ab_0        

In [9]:
#| export
%time
import os
import glob
import numpy as np
import nrrd
import cv2
import matplotlib.pyplot as plt
from ipywidgets import interact, interactive, IntSlider, ToggleButtons
from scipy import ndimage


# Función para extraer rodajas en diferentes ángulos y planos
def extract_slices(data, angle, plane, rotation_axis):
    # Rotar la imagen 3D
    if rotation_axis == 'xy':
        rotated_data = ndimage.rotate(data, angle, axes=(1, 0), reshape=True)
    elif rotation_axis == 'xz':
        rotated_data = ndimage.rotate(data, angle, axes=(2, 0), reshape=True)
    elif rotation_axis == 'yz':
        rotated_data = ndimage.rotate(data, angle, axes=(2, 1), reshape=True)

    # Extraer rodajas en función del plano especificado
    slices = []
    x_size, y_size, z_size = rotated_data.shape

    if plane == 'x':
        for i in range(x_size):
            slices.append(rotated_data[i, :, :])
    elif plane == 'y':
        for i in range(y_size):
            slices.append(rotated_data[:, i, :])
    elif plane == 'z':
        for i in range(z_size):
            slices.append(rotated_data[:, :, i])

    return slices



# Función para guardar las rodajas en una estructura de carpetas
def save_slices(slices, output_dir, plane, angle, rotation_axis):
    # Crear la estructura de carpetas
    plane_dir = os.path.join(output_dir, f"Plano{plane.upper()}")
    os.makedirs(plane_dir, exist_ok=True)

    rotation_dir = os.path.join(plane_dir, f"Rotacion{rotation_axis.upper()}")
    os.makedirs(rotation_dir, exist_ok=True)

    angle_dir = os.path.join(rotation_dir, f"Angulo{angle}")
    os.makedirs(angle_dir, exist_ok=True)

    # Guardar las rodajas en la carpeta correspondiente
    for idx, slice_data in enumerate(slices):
        slice_file = os.path.join(angle_dir, f"{plane.upper()}_{rotation_axis.upper()}_{angle}_{idx}.png")
        cv2.imwrite(slice_file, slice_data)

def read_nrrd_file(filename):
    data, header = nrrd.read(filename)
    return data, header


def main(input_dir, output_dir):
    # Obtener todos los archivos NRRD en el directorio de entrada
    nrrd_files = glob.glob(os.path.join(input_dir, "*.nrrd"))

    # Procesar cada archivo NRRD
    for nrrd_file in nrrd_files:
        print(f"Procesando {nrrd_file}")

        # Leer el archivo NRRD y obtener sus dimensiones
        

        try:
            data,header = read_nrrd_file(nrrd_file)
            
        except Exception as e:
            print(f"Error al leer el archivo {nrrd_file}: {str(e)}")
            continue
        print(f"Dimensiones de la imagen: {data.shape}")
        print(f"Rango de movimiento (x, y, z): {header['sizes']}")

        # Extraer y guardar rodajas en diferentes ángulos y planos
        angles = [0, 45]
        planes = ['x', 'y', 'z']
        rotation_axes = ['xy', 'xz', 'yz']

        for plane in planes:
            for angle in angles:
                for rotation_axis in rotation_axes:
                    slices = extract_slices(data, angle, plane, rotation_axis)
                    save_slices(slices, output_dir, plane, angle, rotation_axis)

if __name__ == "__main__":
    input_dir = "archivos_nrrd"  # Directorio con los archivos NRRD
    output_dir = "dataset"  # Directorio donde se guardarán las rodajas
    main(input_dir, output_dir)

CPU times: user 5 µs, sys: 2 µs, total: 7 µs
Wall time: 10.7 µs
Procesando archivos_nrrd/4075542_2015_10_04.nrrd
Dimensiones de la imagen: (199, 203, 211)
Rango de movimiento (x, y, z): [199 203 211]


In [ ]:
!zip -r slices_output.zip "/dataset"



In [ ]:
from nbdev import *


In [ ]:
learn_gen.load("gen-pre2")

In [ ]:
from pathlib import Path
name_gen = "image_gen"
path=Path('content')
path_gen = path/name_gen

In [ ]:
# shutil.rmtree(path_gen)

In [ ]:
path_gen.mkdir(exist_ok=True)